### 1 - Import test data

In [16]:
import pandas as pd
import pandas_ta as ta

df = pd.read_csv('clean15.csv')
df.rename(columns={'datetime' : 'Gmt time', 'close' : 'Close', 'high': 'High', 'open' : 'Open', 'low':'Low'}, inplace=True)
# df = pd.read_csv("EURUSD_Candlestick_5_M_ASK_30.09.2019-30.09.2022.csv")
df["Gmt time"]=df["Gmt time"].str.replace(".000","")
df['Gmt time']=pd.to_datetime(df['Gmt time'],format='%Y-%m-%d %H:%M:%S')
df=df[df.High!=df.Low]
df.set_index("Gmt time", inplace=True)

In [17]:
df["EMA_slow"]=ta.ema(df.Close, length=50)
df["EMA_fast"]=ta.ema(df.Close, length=30)
df['RSI']=ta.rsi(df.Close, length=10)
my_bbands = ta.bbands(df.Close, length=15, std=1.5)
df['ATR']=ta.atr(df.High, df.Low, df.Close, length=7)
df=df.join(my_bbands)
df

Open     High      Low    Close  volume  EMA_slow  \
Gmt time                                                                    
2002-10-21 01:05:00  0.97320  0.97325  0.97280  0.97285       0       NaN   
2002-10-21 01:10:00  0.97300  0.97320  0.97300  0.97320       0       NaN   
2002-10-21 01:15:00  0.97320  0.97320  0.97295  0.97310       0       NaN   
2002-10-21 01:20:00  0.97315  0.97340  0.97270  0.97270       0       NaN   
2002-10-21 01:25:00  0.97280  0.97295  0.97260  0.97260       0       NaN   
...                      ...      ...      ...      ...     ...       ...   
2020-06-04 19:25:00  1.13419  1.13421  1.13402  1.13402     438  1.133783   
2020-06-04 19:30:00  1.13401  1.13402  1.13368  1.13398     585  1.133791   
2020-06-04 19:35:00  1.13399  1.13411  1.13395  1.13396     495  1.133797   
2020-06-04 19:40:00  1.13396  1.13403  1.13386  1.13398     508  1.133804   
2020-06-04 19:45:00  1.13399  1.13406  1.13388  1.13394     493  1.133810   

                     EMA_fast        RSI       ATR  BBL_15_1.5  BBM_15_1.5  \
Gmt time                                                                     
2002-10-21 01:05:00       NaN        NaN       NaN         NaN         NaN   
2002-10-21 01:10:00       NaN        NaN       NaN         NaN         NaN   
2002-10-21 01:15:00       NaN        NaN       NaN         NaN         NaN   
2002-10-21 01:20:00       NaN        NaN       NaN         NaN         NaN   
2002-10-21 01:25:00       NaN        NaN       NaN         NaN         NaN   
...                       ...        ...       ...         ...         ...   
2020-06-04 19:25:00  1.133922  51.314980  0.000280    1.133591    1.134015   
2020-06-04 19:30:00  1.133926  50.097358  0.000289    1.133592    1.133987   
2020-06-04 19:35:00  1.133928  49.445545  0.000270    1.133588    1.133967   
2020-06-04 19:40:00  1.133932  50.165975  0.000256    1.133598    1.133941   
2020-06-04 19:45:00  1.133932  48.626086  0.000245    1.133593    1.133929   

                     BBU_15_1.5  BBB_15_1.5  BBP_15_1.5  
Gmt time                                                 
2002-10-21 01:05:00         NaN         NaN         NaN  
2002-10-21 01:10:00         NaN         NaN         NaN  
2002-10-21 01:15:00         NaN         NaN         NaN  
2002-10-21 01:20:00         NaN         NaN         NaN  
2002-10-21 01:25:00         NaN         NaN         NaN  
...                         ...         ...         ...  
2020-06-04 19:25:00    1.134440    0.074837    0.505499  
2020-06-04 19:30:00    1.134383    0.069723    0.490725  
2020-06-04 19:35:00    1.134345    0.066801    0.491199  
2020-06-04 19:40:00    1.134284    0.060473    0.557360  
2020-06-04 19:45:00    1.134265    0.059281    0.515868  

[1329213 rows x 14 columns]

In [18]:
def ema_signal(df, current_candle, backcandles):
    df_slice = df.reset_index().copy()
    # Get the range of candles to consider
    start = max(0, current_candle - backcandles)
    end = current_candle
    relevant_rows = df_slice.iloc[start:end]

    # Check if all EMA_fast values are below EMA_slow values
    if all(relevant_rows["EMA_fast"] < relevant_rows["EMA_slow"]):
        return 1
    elif all(relevant_rows["EMA_fast"] > relevant_rows["EMA_slow"]):
        return 2
    else:
        return 0


df=df[-30000:-1]
from tqdm import tqdm
tqdm.pandas()
df.reset_index(inplace=True)
df['EMASignal'] = df.progress_apply(lambda row: ema_signal(df, row.name, 7) , axis=1) #if row.name >= 20 else 0

100%|██████████| 29999/29999 [01:51<00:00, 269.47it/s]
C:\Users\S.Eyvazi\AppData\Local\Temp\ipykernel_29444\389014093.py:21: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [19]:
def total_signal(df, current_candle, backcandles):
    if (ema_signal(df, current_candle, backcandles)==2
        and df.Close[current_candle]<=df['BBL_15_1.5'][current_candle]
        #and df.RSI[current_candle]<60
        ):
            return 2
    if (ema_signal(df, current_candle, backcandles)==1
        and df.Close[current_candle]>=df['BBU_15_1.5'][current_candle]
        #and df.RSI[current_candle]>40
        ):
    
            return 1
    return 0
        
df['TotalSignal'] = df.progress_apply(lambda row: total_signal(df, row.name, 7), axis=1)

100%|██████████| 29999/29999 [03:49<00:00, 130.62it/s]
C:\Users\S.Eyvazi\AppData\Local\Temp\ipykernel_29444\33230926.py:15: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [20]:
df[df.TotalSignal != 0].head(20)

Gmt time     Open     High      Low    Close  volume  EMA_slow  \
3   2020-01-13 08:30:00  1.11203  1.11256  1.11203  1.11253     940  1.112177   
60  2020-01-13 13:15:00  1.11400  1.11401  1.11377  1.11382     201  1.113665   
68  2020-01-13 13:55:00  1.11394  1.11403  1.11374  1.11380     519  1.113728   
69  2020-01-13 14:00:00  1.11380  1.11380  1.11371  1.11371     199  1.113727   
70  2020-01-13 14:05:00  1.11372  1.11377  1.11367  1.11375     247  1.113728   
73  2020-01-13 14:20:00  1.11377  1.11381  1.11368  1.11370     195  1.113730   
75  2020-01-13 14:30:00  1.11375  1.11379  1.11363  1.11363     207  1.113727   
76  2020-01-13 14:35:00  1.11362  1.11372  1.11360  1.11361     255  1.113723   
83  2020-01-13 15:10:00  1.11368  1.11372  1.11351  1.11356     176  1.113710   
84  2020-01-13 15:15:00  1.11356  1.11359  1.11341  1.11342     144  1.113698   
89  2020-01-13 15:40:00  1.11356  1.11357  1.11338  1.11338     124  1.113668   
90  2020-01-13 15:45:00  1.11337  1.11341  1.11327  1.11328     196  1.113653   
98  2020-01-13 16:25:00  1.11362  1.11378  1.11360  1.11369     135  1.113611   
117 2020-01-13 18:00:00  1.11342  1.11372  1.11338  1.11372     515  1.113585   
118 2020-01-13 18:05:00  1.11372  1.11379  1.11368  1.11378     374  1.113592   
119 2020-01-13 18:10:00  1.11377  1.11382  1.11371  1.11374     556  1.113598   
120 2020-01-13 18:15:00  1.11373  1.11383  1.11370  1.11382     323  1.113607   
134 2020-01-13 19:25:00  1.11372  1.11379  1.11346  1.11349     589  1.113703   
135 2020-01-13 19:30:00  1.11348  1.11362  1.11328  1.11336     775  1.113690   
136 2020-01-13 19:35:00  1.11336  1.11354  1.11326  1.11328     701  1.113674   

     EMA_fast        RSI       ATR  BBL_15_1.5  BBM_15_1.5  BBU_15_1.5  \
3    1.112172  63.432027  0.000302    1.111809    1.112155    1.112501   
60   1.113883  42.891381  0.000194    1.113828    1.114054    1.114280   
68   1.113887  42.522787  0.000169    1.113815    1.113921    1.114027   
69   1.113876  38.342772  0.000157    1.113775    1.113902    1.114029   
70   1.113867  41.197263  0.000149    1.113751    1.113888    1.114025   
73   1.113846  38.729497  0.000144    1.113709    1.113847    1.113984   
75   1.113826  36.243471  0.000140    1.113670    1.113817    1.113965   
76   1.113812  35.214350  0.000137    1.113639    1.113795    1.113951   
83   1.113759  34.979198  0.000135    1.113604    1.113693    1.113783   
84   1.113737  28.014810  0.000141    1.113538    1.113674    1.113810   
89   1.113678  32.724131  0.000124    1.113457    1.113602    1.113747   
90   1.113652  28.712720  0.000127    1.113391    1.113579    1.113767   
98   1.113593  59.968312  0.000183    1.113281    1.113485    1.113689   
117  1.113570  61.815316  0.000135    1.113453    1.113553    1.113654   
118  1.113583  64.906787  0.000131    1.113434    1.113563    1.113692   
119  1.113593  61.234486  0.000128    1.113442    1.113581    1.113720   
120  1.113608  65.564081  0.000129    1.113435    1.113599    1.113764   
134  1.113737  38.166317  0.000223    1.113604    1.113846    1.114088   
135  1.113713  34.297190  0.000240    1.113512    1.113815    1.114118   
136  1.113685  32.073936  0.000245    1.113414    1.113777    1.114139   

     BBB_15_1.5  BBP_15_1.5  EMASignal  TotalSignal  
3      0.062209    1.041539          1            1  
60     0.040611   -0.017203          2            2  
68     0.019040   -0.072073          2            2  
69     0.022836   -0.254807          2            2  
70     0.024551   -0.004632          2            2  
73     0.024659   -0.033987          2            2  
75     0.026472   -0.135354          2            2  
76     0.028041   -0.091274          2            2  
83     0.016122   -0.242578          2            2  
84     0.024350   -0.436664          2            2  
89     0.026123   -0.263144          2            2  
90     0.033776   -0.294079          2            2  
98     0.036637    1.001694          1            1  
11

In [21]:
import numpy as np
def pointpos(x):
    if x['TotalSignal']==2:
        return x['Low']-1e-3
    elif x['TotalSignal']==1:
        return x['High']+1e-3
    else:
        return np.nan

df['pointpos'] = df.apply(lambda row: pointpos(row), axis=1)

C:\Users\S.Eyvazi\AppData\Local\Temp\ipykernel_29444\177647043.py:10: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [22]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from datetime import datetime
st=100
dfpl = df[st:st+350]
#dfpl.reset_index(inplace=True)
fig = go.Figure(data=[go.Candlestick(x=dfpl.index,
                open=dfpl['Open'],
                high=dfpl['High'],
                low=dfpl['Low'],
                close=dfpl['Close']),

                go.Scatter(x=dfpl.index, y=dfpl['BBL_15_1.5'], 
                           line=dict(color='green', width=1), 
                           name="BBL"),
                go.Scatter(x=dfpl.index, y=dfpl['BBU_15_1.5'], 
                           line=dict(color='green', width=1), 
                           name="BBU"),
                go.Scatter(x=dfpl.index, y=dfpl['EMA_fast'], 
                           line=dict(color='black', width=1), 
                           name="EMA_fast"),
                go.Scatter(x=dfpl.index, y=dfpl['EMA_slow'], 
                           line=dict(color='blue', width=1), 
                           name="EMA_slow")])

fig.add_scatter(x=dfpl.index, y=dfpl['pointpos'], mode="markers",
                marker=dict(size=5, color="MediumPurple"),
                name="entry")

fig.show()

In [23]:
def SIGNAL():
    return df.TotalSignal

In [24]:
from backtesting import Strategy
from backtesting import Backtest

class MyStrat(Strategy):
    mysize = 3000
    slcoef = 1.894736
    TPSLRatio = 1.05263
    rsi_length = 16
    
    def init(self):
        super().init()
        self.signal1 = self.I(SIGNAL)
        #df['RSI']=ta.rsi(df.Close, length=self.rsi_length)

    def next(self):
        super().next()
        slatr = self.slcoef*self.data.ATR[-1]
        TPSLRatio = self.TPSLRatio

        # if len(self.trades)>0:
        #     if self.trades[-1].is_long and self.data.RSI[-1]>=90:
        #         self.trades[-1].close()
        #     elif self.trades[-1].is_short and self.data.RSI[-1]<=10:
        #         self.trades[-1].close()
        
        if self.data.TotalSignal==2 and len(self.trades)==0:
            sl1 = self.data.Close[-1] - slatr
            tp1 = self.data.Close[-1] + slatr*TPSLRatio
            self.buy(sl=sl1, tp=tp1, size=self.mysize)
        
        elif self.data.TotalSignal==1 and len(self.trades)==0:         
            sl1 = self.data.Close[-1] + slatr
            tp1 = self.data.Close[-1] - slatr*TPSLRatio
            self.sell(sl=sl1, tp=tp1, size=self.mysize)

bt = Backtest(df, MyStrat, cash=250, margin=1/30)

C:\Users\S.Eyvazi\AppData\Local\Temp\ipykernel_29444\3637604655.py:36: UserWarning:

Data index is not datetime. Assuming simple periods, but `pd.DateTimeIndex` is advised.



In [25]:
bt.run()

Start                                     0.0
End                                   29998.0
Duration                              29998.0
Exposure Time [%]                   43.764792
Equity Final [$]                   450.799808
Equity Peak [$]                    506.484517
Return [%]                          80.319923
Buy & Hold Return [%]                1.967449
Return (Ann.) [%]                         0.0
Volatility (Ann.) [%]                     NaN
Sharpe Ratio                              NaN
Sortino Ratio                             NaN
Calmar Ratio                              0.0
Max. Drawdown [%]                  -17.346325
Avg. Drawdown [%]                   -1.410868
Max. Drawdown Duration                12223.0
Avg. Drawdown Duration             218.238462
# Trades                               1149.0
Win Rate [%]                        50.391645
Best Trade [%]                       0.441938
Worst Trade [%]                     -0.397462
Avg. Trade [%]                    

In [26]:
bt.plot()

GridPlot(id='p1613', ...)

In [27]:
stats = bt.optimize(TPSLRatio=np.linspace(1, 2, 20).tolist(),
                    slcoef=np.linspace(1, 2, 20).tolist(),
                    maximize='Equity Final [$]')

E:\Project\Farabi\StockMarketData\venv\Lib\site-packages\backtesting\backtesting.py:1488: UserWarning:

Searching for best of 400 configurations.



  0%|          | 0/16 [00:00<?, ?it/s]

In [28]:
stats

Start                                     0.0
End                                   29998.0
Duration                              29998.0
Exposure Time [%]                   43.764792
Equity Final [$]                   450.802368
Equity Peak [$]                    506.486277
Return [%]                          80.320947
Buy & Hold Return [%]                1.967449
Return (Ann.) [%]                         0.0
Volatility (Ann.) [%]                     NaN
Sharpe Ratio                              NaN
Sortino Ratio                             NaN
Calmar Ratio                              0.0
Max. Drawdown [%]                  -17.346159
Avg. Drawdown [%]                   -1.410864
Max. Drawdown Duration                12223.0
Avg. Drawdown Duration             218.238462
# Trades                               1149.0
Win Rate [%]                        50.391645
Best Trade [%]                       0.441938
Worst Trade [%]                     -0.397462
Avg. Trade [%]                    

In [29]:
np.linspace(1, 3, 20).tolist()


[1.0,
 1.1052631578947367,
 1.2105263157894737,
 1.3157894736842106,
 1.4210526315789473,
 1.526315789473684,
 1.631578947368421,
 1.736842105263158,
 1.8421052631578947,
 1.9473684210526314,
 2.052631578947368,
 2.1578947368421053,
 2.263157894736842,
 2.3684210526315788,
 2.473684210526316,
 2.5789473684210527,
 2.6842105263157894,
 2.789473684210526,
 2.894736842105263,
 3.0]

In [30]:
stats._strategy


<Strategy MyStrat(TPSLRatio=1.0526315789473684,slcoef=1.894736842105263)>